# TO DO

- pyLDAviz (write code)
- LDA (rerun through)
- LSA (rerun through)
- NMF (rerun through)

how do these impact project and what can I gleen from it? 



Once I have topics:
- assign topics to documents
- look at sentiment across different topics
    - dataframe: topic, document, sentiment (3 columns)
    - e.g. might see, 3rd trimester --> negative sentiment, but 6 wks --> positive sentiment


If time for predictive model:
- can I predict what side of the debate the person is on based on sentiment?

In [ ]:
# sentiment analysis
# positive vs negative verbal statement based on sentiment of post

# use packages that analyze the writing level - is there a difference in level of intelligence of dif people on dif subreddits?
# might have dif viewpoints in each subreddit - try to do some tagging of dif viewpoints in each subreddit; averaging of snetiment and averaging of level of intelligence
# to do tagging of dif viewpoints - based on sentiment?
# length of post

In [2]:
from __future__ import print_function


import pickle

import time
import pandas as pd
import numpy as np

import matplotlib.pyplot as plt
import matplotlib.patheffects as PathEffects
%matplotlib inline

import seaborn as sns
sns.set_style('darkgrid')
sns.set_palette('muted')
sns.set_context("notebook", font_scale=1.5,
                rc={"lines.linewidth": 2.5})
RS = 123

import csv, re

import nltk
import string
from html.parser import HTMLParser

from nltk.corpus import stopwords
from nltk.stem.wordnet import WordNetLemmatizer
from sklearn import datasets
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.decomposition import TruncatedSVD, NMF, LatentDirichletAllocation, PCA
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.preprocessing import scale
from sklearn.cluster import KMeans
from sklearn.datasets import make_blobs, fetch_mldata
from sklearn.utils import shuffle
from sklearn.manifold import TSNE

from vaderSentiment.vaderSentiment import SentimentIntensityAnalyzer

import pyLDAvis
import pyLDAvis.sklearn
pyLDAvis.enable_notebook()

# see https://ipython.readthedocs.io/en/stable/interactive/magics.html
%pylab inline

# sets backend to render higher res images
%config InlineBackend.figure_formats = ['retina']


# gensim
from gensim import corpora, models, similarities, matutils

# logging for gensim (set to INFO)
import logging
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)

# from wordcloud import WordCloud, STOPWORDS , ImageColorGenerator


Populating the interactive namespace from numpy and matplotlib


/Users/laurenfinkelstein/anaconda3/lib/python3.7/site-packages/IPython/core/magics/pylab.py:160: UserWarning: pylab import has clobbered these variables: ['shuffle']
`%matplotlib` prevents importing * from pylab and numpy
  "\n`%matplotlib` prevents importing * from pylab and numpy"
/Users/laurenfinkelstein/anaconda3/lib/python3.7/site-packages/smart_open/ssh.py:34: UserWarning: paramiko missing, opening SSH/SCP/SFTP paths will be disabled.  `pip install paramiko` to suppress
  warnings.warn('paramiko missing, opening SSH/SCP/SFTP paths will be disabled.  `pip install paramiko` to suppress')
/Users/laurenfinkelstein/anaconda3/lib/python3.7/site-packages/scipy/sparse/sparsetools.py:21: DeprecationWarning: `scipy.sparse.sparsetools` is deprecated!
scipy.sparse.sparsetools is a private module for scipy.sparse, and should not be used.
  _deprecated()


In [3]:
# load in data

corpus = pickle.load(open('reproductive_rights_corpus3_clean.pkl', 'rb'))
# count_vecs = pickle.load(open('reproductive_count_vecs_bag_of_words.pkl', 'rb'))
# tfidf_vecs = pickle.load(open('reproductive_rights_tfidf.pkl', 'rb'))

In [ ]:
len(corpus)

In [ ]:
corpus

# Tokenization

### Count Vectorize

In [ ]:
# CV 1

cv = CountVectorizer(ngram_range=(2,4), max_df=.95, min_df=30, stop_words='english')
# cv = CountVectorizer(ngram_range=(2,4), max_df=.95, min_df=30, 
#                      stop_words=frozenset(['reddit', 'subreddit', 'prolife', 'prochoice', 'pro choicers', 'pro lifers', 'abortion', 'pro life', 'pro choice', 'pro abortion',
#                          'rprolife', 'rprochoice', 'prolifers', 'prochoicers', 'prolifer', 'prochoicer']))
X_cv = cv.fit_transform(corpus)
count_vecs = pd.DataFrame(X_cv.toarray(), index=corpus, columns=cv.get_feature_names())

In [ ]:
X_cv

In [ ]:
count_vecs.shape

### TFIDF

In [ ]:
word_vectorizer = TfidfVectorizer(
    sublinear_tf=True,
    strip_accents='unicode',
    analyzer='word',
    token_pattern=r'\w{1,}',
    ngram_range=(2, 4),
    max_df=0.95,
    min_df=30,
    stop_words='english')

X_wv = word_vectorizer.fit_transform(corpus)

tfidf_vecs = pd.DataFrame(X_wv.toarray(), index=corpus, columns=word_vectorizer.get_feature_names())

In [ ]:
tfidf_vecs.shape

# Topic Modeling

## Py LDA Vis

In [ ]:
lda_cv = LatentDirichletAllocation(n_topics=5, random_state=0)
lda_cv.fit(count_vecs)

In [ ]:
pyLDAvis.sklearn.prepare(lda_cv, X_cv, cv)

## Latent Semantic Analysis (LSA)

> Note: LSA is SVD applied to NLP

### LSA on TF-IDF

In [ ]:
lsa = TruncatedSVD(3) # start low and then increase so you can see the differentiation between them; get a sense of how they cluster the more you add onto it (instead of working big and then working down)
topics_tfidf = lsa.fit_transform(tfidf_vecs)
lsa.explained_variance_ratio_

The U matrix shows us the resulting topics, and the terms that are associated with each topic. In this case:

In [ ]:
def display_topics(model, feature_names, no_top_words, topic_names=None):
    for ix, topic in enumerate(model.components_):
        if not topic_names or not topic_names[ix]:
            print("\nTopic ", ix)
        else:
            print("\nTopic: '",topic_names[ix],"'")
        print(", ".join([feature_names[i]
                        for i in topic.argsort()[:-no_top_words - 1:-1]]))

In [ ]:
display_topics(lsa, word_vectorizer.get_feature_names(), 7)

The Vt matrix shows us the documents we started with, and how each document is made up of the resulting topics. 

In [ ]:
Vt_tfidf = pd.DataFrame(topics_tfidf.round(5),
             index = corpus,
             columns = ["component_1","component_2", "component_3"])
Vt_tfidf.head()

### LSA on Count Vectorizer

In [ ]:
lsa = TruncatedSVD(3)
lsa_cv = lsa.fit_transform(count_vecs)
lsa.explained_variance_ratio_

# first topic captures 9.5%, second topic captures 4%

The U matrix shows us the 2 resulting topics, and the terms that are associated with each topic. In this case:
- Component 1 (topic 1) seems to be about ?
- Component 2 (topic 2) seems to be about ?

In [ ]:
display_topics(lsa, cv.get_feature_names(), 7)

The Vt matrix shows us the documents we started with, and how each document is made up of the 2 resulting topics. In this case:
- The first four documents seem to be about ?
- The last three documents seem to be about ?

In [ ]:
Vt_cv = pd.DataFrame(lsa_cv.round(5),
             index = corpus,
             columns = ["component_1","component_2", "component_3"])
Vt_cv.head()

## Non-Negative Matrix Factorization (NMF)

### NMF on TFIDF

In [ ]:
nmf_model_tfidf = NMF(3)
doc_topic_nmf_tfidf = nmf_model_tfidf.fit_transform(X_wv)

The W matrix shows us the 2 resulting topics, and the terms that are associated with each topic. In this case:
- Component 1 (topic 1) seems to be about ?
- Component 2 (topic 2) seems to be about ?

In [ ]:
display_topics(nmf_model_tfidf, word_vectorizer.get_feature_names(), 7)

# Note - if you need more than 25 words to figure out the pattern, your topic buckets may be too big
# might have independent subthemes living in the buckets; need smaller more tailored buckets

##### The H matrix shows us the documents we started with, and how each document is made up of the 2 resulting topics. In this case:
- The first document seems to be about music
- The last document seems to be about sports
- Everything in between is a combination of the two

In [ ]:
ex_label = [c[:30]+"..." for c in corpus]

H_tfidf = pd.DataFrame(doc_topic_nmf_tfidf.round(5),
             index = ex_label,
             columns = ["component_1","component_2", "component_3"])
H_tfidf.head()

# things don't necessary add up to 1 or the same thing
# some are more generic discussions that don't necessarily have a strong tie in with music or sports
# could also generate a document with strong tie in to both

### NMF on Count Vectorizer

In [ ]:
nmf_model_cv = NMF(3)
doc_topic_nmf_cv = nmf_model_cv.fit_transform(X_cv)

The W matrix shows us the 2 resulting topics, and the terms that are associated with each topic. In this case:
- Component 1 (topic 1) seems to be about ?
- Component 2 (topic 2) seems to be about ?

In [ ]:
display_topics(nmf_model_cv, cv.get_feature_names(), 7)

# Note - if you need more than 25 words to figure out the pattern, your topic buckets may be too big
# might have independent subthemes living in the buckets; need smaller more tailored buckets

The H matrix shows us the documents we started with, and how each document is made up of the 2 resulting topics. In this case:
- The first document seems to be about ?
- The last document seems to be about ?
- Everything in between is a combination of the two

In [ ]:
H_cv = pd.DataFrame(doc_topic_nmf_cv.round(5),
             index = ex_label,
             columns = ["component_1","component_2", "component_3"])
H_cv.head()

# things don't necessary add up to 1 or the same thing
# some are more generic discussions that don't necessarily have a strong tie in with music or sports
# could also generate a document with strong tie in to both

In [ ]:
H_cv_fake = H_cv
H_cv_fake['component_4']  = H_cv_fake['component_1'] + H_cv_fake['component_2'] + H_cv_fake['component_3']

In [ ]:
H_cv_fake[H_cv_fake['component_4'] == 0] =1

In [ ]:
H_cv_topics = H_cv_fake.idxmax(axis=1)

In [ ]:
H_cv_topics.head()

##### Reducing to 2D with t-SNE

In [ ]:
## THIS WAS TAKING TOO LONG -- do word2vec and THEN do this so its reduced and runs faster

In [ ]:
# a t-SNE model
# angle value close to 1 means sacrificing accuracy for speed
# pca initializtion usually leads to better results 
tsne_model = TSNE(n_components=2, verbose=1, random_state=0, angle=.99, init='pca')

# 20-D -> 2-D
tsne_lda = tsne_model.fit_transform(X_cv.toarray())

# PCA

### PCA on Count Vectorizer

In [ ]:
pca_cv = PCA(n_components=3) # try higher components
pca_cv.fit(count_vecs)
pcafeatures_train_cv = pca_cv.transform(count_vecs)

In [ ]:
pca_cv.explained_variance_ratio_

In [ ]:
# to get vectors

pca_cv.components[:3]

In [ ]:
display_topics(pca_cv, cv.get_feature_names(), 7)

In [ ]:
from itertools import cycle

def plot_PCA_2D(data, target, target_names):
    colors = cycle(['r','g','b','c','m','y','orange','w','aqua','yellow'])
    target_ids = range(len(target_names))
    plt.figure(figsize=(5,5))
    for i, c, label in zip(target_ids, colors, target_names):
        ax = plt.scatter(data[target == i, 0], data[target == i, 1],
                   c=c, label=label, edgecolors='gray')
    
    plt.legend()



# other colours: ,'m','y','orange','w','aqua','yellow'

In [ ]:
# plot graph to see elbow of how many components to include

plt.plot(pca_cv.explained_variance_ratio_)
plt.xlabel('# components')
plt.ylabel('explained variance');
plt.title('Scree plot for reddit comments');

In [ ]:
pd.DataFrame(pcafeatures_train_cv)

In [ ]:
## WHAT SHOULD TARGET = ?

target_names = [0, 1, 2]

plot_PCA_2D(pcafeatures_train_cv, target=count_vecs, target_names=target_names)

### PCA on TF-IDF

In [ ]:
pca_tfidf = PCA(n_components=3) 
pca_tfidf.fit(tfidf_vecs)
pcafeatures_train_tfidf = pca_tfidf.transform(tfidf_vecs)

In [ ]:
pca_tfidf.explained_variance_ratio_

In [ ]:
# plot graph to see elbow of how many components to include

plt.plot(pca_tfidf.explained_variance_ratio_)
plt.xlabel('# components')
plt.ylabel('explained variance');
plt.title('Scree plot for reddit comments');

In [ ]:
pd.DataFrame(pcafeatures_train_tfidf)

In [ ]:
## WHAT SHOULD MY TARGET BE SET TO? THIS IS LEE'S CODE, AND HER'S WAS LABELED

target_names = [0, 1, 2]

plot_PCA_2D(pcafeatures_train_tfidf, target=df.emotion, target_names=target_names)

# T-SNE to visualize clusters

In [ ]:
# Utility function to visualize the outputs of PCA and t-SNE

def scatter(x, colors):
    # choose a color palette with seaborn.
    num_classes = len(np.unique(colors))
    palette = np.array(sns.color_palette("hls", num_classes))

    # create a scatter plot.
    f = plt.figure(figsize=(8, 8))
    ax = plt.subplot(aspect='equal')
    sc = ax.scatter(x[:,0], x[:,1], lw=0, s=40, c=palette[colors.astype(np.int)])
    plt.xlim(-25, 25)
    plt.ylim(-25, 25)
    ax.axis('off')
    ax.axis('tight')

    # add the labels for each digit corresponding to the label
    txts = []

    for i in range(num_classes):

        # Position of each label at median of data points.

        xtext, ytext = np.median(x[colors == i, :], axis=0)
        txt = ax.text(xtext, ytext, str(i), fontsize=24)
        txt.set_path_effects([
            PathEffects.Stroke(linewidth=5, foreground="w"),
            PathEffects.Normal()])
        txts.append(txt)

    return f, ax, sc, txts

In [ ]:
# NMF T-SNE
tsne = TSNE(random_state=RS).fit_transform(X_cv) # change x_subset

In [ ]:
scatter(tsne, H_cv_topics) # change y_subset to my topics?

In [ ]:
# PCA T-SNE
tsne = TSNE(random_state=RS).fit_transform(pcafeatures_train)

In [ ]:
scatter(tsne, df.emotion)

In [ ]:
# 3D t-SNE plot code

from mpl_toolkits.mplot3d import Axes3D
import matplotlib.pyplot as plt



fig = plt.figure()
ax = fig.add_subplot(111, projection='3d')

x =pd.DataFrame(tsne_3d).loc[:,0]
y2 =pd.DataFrame(tsne_3d).loc[:,1]
z =pd.DataFrame(tsne_3d).loc[:,2]



ax.scatter(x, y2, z, c=df.emotion, marker='o', )

ax.set_xlabel('X Label')
ax.set_ylabel('Y Label')
ax.set_zlabel('Z Label')

plt.show()

In [ ]:
# tsne with 3 components

tsne = TSNE(random_state=RS, n_components=3).fit_transform(nmf_topics)

# Word 2 Vec

In [ ]:
# convo with Han Wei -- matrix will be # rows I have (1.3k) * 300
    # when Google trained this model, they set the dimension as 300
# Can also try Glove (similar to Word2Vec); Stanford trained this model
    # they set the components to 100

# Word Clouds

# Sentiment Analysis

- if vader works do vader, if not do wordblob

In [ ]:
## QUESTION - should emojis be kept in text for this?

# https://medium.com/analytics-vidhya/simplifying-social-media-sentiment-analysis-using-vader-in-python-f9e6ec6fc52f

In [4]:
analyser = SentimentIntensityAnalyzer()

In [5]:
# use the polarity_scores() method to obtain the polarity indices for the given sentence

def sentiment_analyzer_scores(sentence):
    score = analyser.polarity_scores(sentence)
    print("{:-<40} {}".format(sentence, str(score)))

In [ ]:
# feed each of my documents into this

sentiment_analyzer_scores("The phone is super cool.")

In [6]:
corpus_sentiment = [sentiment_analyzer_scores(c) for c in corpus]
corpus_sentiment[:10]

child deserve love want right force woman gestate birth child want care forthe good way reduce demand make birth control free available antiabortion law make illegal common lead dead pregnant woman believe fantasy think {'neg': 0.186, 'neu': 0.494, 'pos': 0.32, 'compound': 0.7003}
yes------------------------------------- {'neg': 0.0, 'neu': 0.0, 'pos': 1.0, 'compound': 0.4019}
definitely agree statement-------------- {'neg': 0.0, 'neu': 0.161, 'pos': 0.839, 'compound': 0.6369}
exfoster kid exact childhood feel deeply {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}
  cheap compare state pay raise kid probably cost like   year {'neg': 0.118, 'neu': 0.672, 'pos': 0.21, 'compound': 0.2732}
publicly fund stop---------------------- {'neg': 0.524, 'neu': 0.476, 'pos': 0.0, 'compound': -0.296}
child bear save money eh love anyways--- {'neg': 0.0, 'neu': 0.403, 'pos': 0.597, 'compound': 0.8126}
hello personally advocate sway issue like hear argument just liberal town just curious point ci

oh want effectively aid prevention support thing list s way conflict political ideal just care idea embryofetus person religious base idea science s fine believe wrong ineffective impose make law medical decision base religious view reason make base fairy tale violate amendment contradict republican claim want small governmentedit way roe v wade prohibit trimester elective politician straight fear monger trimester unless threat life severe abnormality point devastating woman disagree elective term limit agree limit elective point gestational age fetus survive independently womb point premature infant support procedure medical reason way birth happenspregnancy dangerous life threatening complication happen normal pregnancy   time safe child birth safe remove birth dc csectioninduction doctor afraid action life threaten complication fear prosecute happen alreadylook past look ireland look china woman afraid come forward want pregnancy miscarry turn septic s death sentence embryofetus wom

low education coincidence think alabama stop fuck cousin {'neg': 0.609, 'neu': 0.391, 'pos': 0.0, 'compound': -0.7783}
make woman marry rapist fucker---------- {'neg': 0.754, 'neu': 0.246, 'pos': 0.0, 'compound': -0.8807}
alabama resident confirm validity statememt {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}
ohioan entire thing sicken literally---- {'neg': 0.42, 'neu': 0.58, 'pos': 0.0, 'compound': -0.4404}
way solve run office seat right--------- {'neg': 0.0, 'neu': 0.735, 'pos': 0.265, 'compound': 0.2023}
alabama hate little girl alabama love rapist hate doctor alabama backwards {'neg': 0.529, 'neu': 0.301, 'pos': 0.169, 'compound': -0.8542}
law strike v vuitch roe v wadethis case   year old roe just sayinthey overturn griswold v connecticut {'neg': 0.103, 'neu': 0.897, 'pos': 0.0, 'compound': -0.128}
welcome think think state like alabama texas georgia ohio just red state worth visit place just proof choice avoid spend money area right onea woman value reproductive choice 

sex solutionim marry want anymore kid logic husband sex anymore problem know solution support sex education focus abstinence sex ed focus baby make thing like ovulation work track ovulation prevent unwanted pregnancy different type birth control consent support easy affordable access birth control thing simple solution help bring rate choose ignore {'neg': 0.105, 'neu': 0.563, 'pos': 0.332, 'compound': 0.9062}
hope people vote guillotine------------- {'neg': 0.0, 'neu': 0.508, 'pos': 0.492, 'compound': 0.4404}
people believe good idea---------------- {'neg': 0.0, 'neu': 0.508, 'pos': 0.492, 'compound': 0.4404}
interesting people protect human extremiststhese forcedbirth extremist protect woman guess woman really human {'neg': 0.0, 'neu': 0.559, 'pos': 0.441, 'compound': 0.7845}
ah yes torture woman bring unwanted child world live abuse foster care poverty {'neg': 0.508, 'neu': 0.267, 'pos': 0.225, 'compound': -0.8126}
guess vegan rightxbbecause human define man woman child species homo

afraid   equally complex personal reason decision fun decision respect easy judge people easy try understand {'neg': 0.0, 'neu': 0.474, 'pos': 0.526, 'compound': 0.9042}
personally think child think efficiently   healthily coparent probably choice   year old single mother   live poverty   look entire group people just like decision right otherslike say feel like fair say justify know individual situation circumstance parent decide good option support {'neg': 0.065, 'neu': 0.629, 'pos': 0.306, 'compound': 0.8834}
murder illegal nice try tho------------- {'neg': 0.634, 'neu': 0.153, 'pos': 0.214, 'compound': -0.7579}
healthy baby abort   week state let healthy baby abort past   week   lateterm just later {'neg': 0.0, 'neu': 0.69, 'pos': 0.31, 'compound': 0.6597}
significant legislation legal social pressure antichoice movement successfully make difficult early number state result woman travel state procedure later date goal make unavailable woman face situation way   make difficult obtai

...

number rule country free speech opinion like sacred law unfortunately fit opinion category vastly different ban form murder large portion country percentage different place united state far far large ireland thing small nation people way simply huge place like stack law protect free speech idea murder just opinion mean backtrack law     solve problem way solve problem provide support way approach fix problem wrong way way people woman wantnee pregnancy general differently need encourage society love woman woman battle finger stretch billion topic like feminism like education like religious freedom church use charity pillar community broad statement say church use charity goto place people needtrouble need program woman scare rape unplanned pregnancy leave abusive relationship just familiar woman plan parenthood mean need place mean need affordable mean need secular woman church alpha center afraid shame afraid catholic planned parenthood care   church sure hell say way roll massive pro

glad open mind situation unwanted child term adoption unfortunately s way happen think unborn child inside woman uterus picture ball cell certainly think point pregnancy longer acceptable   week limit think child think memory remember like bear child life know nothingness great allow grow adult far child concern know life reason fan know choice government say happen friend girlfriend mother woman body {'neg': 0.057, 'neu': 0.658, 'pos': 0.286, 'compound': 0.9468}
despicable------------------------------ {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}
look like license plate----------------- {'neg': 0.0, 'neu': 0.545, 'pos': 0.455, 'compound': 0.3612}
monster--------------------------------- {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}
lady fall purpose----------------------- {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}
agree harass woman seek medical treatment uncalled {'neg': 0.299, 'neu': 0.467, 'pos': 0.234, 'compound': -0.1779}
fractured femur surgery rehab 

convict court public opinion stand white dudexb make sensexbit sadly make twisted sense think really ontopic subredditxb {'neg': 0.149, 'neu': 0.851, 'pos': 0.0, 'compound': -0.4215}
surprise people clip context make absolute truth like hitl ask happen start record context damn important people jump gun fast cause damage people life undo matter try spread actual truth {'neg': 0.2, 'neu': 0.507, 'pos': 0.292, 'compound': 0.2023}
major resistance narrative bubble fast law firm head ryan barne think s threaten libel case behalf kid cnn jack tapper twitter allude completely mischaracterize publication retractingupdate twitter user delete tweet learn know friend just unhappy thing {'neg': 0.133, 'neu': 0.788, 'pos': 0.079, 'compound': -0.296}
  quite clearly plan antagonistic action discredit walk life trump administrationi disagree crazy black dude crazy indian dude demonstrate   day year dc just unlucky run kidsthe medium advantage course {'neg': 0.277, 'neu': 0.589, 'pos': 0.134, 'compou

  burden lifeit kind funny leftist look conservative supposedly espouse pull bootstrap philosophy suddenly use philosophy come fetus bear disabled poor unwanted {'neg': 0.262, 'neu': 0.53, 'pos': 0.209, 'compound': -0.1531}
say------------------------------------- {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}
happy good thing read month thank------- {'neg': 0.0, 'neu': 0.248, 'pos': 0.752, 'compound': 0.8442}
really doubt iq   stop retard----------- {'neg': 0.812, 'neu': 0.188, 'pos': 0.0, 'compound': -0.8251}
believe doctor say little severely damage destroy fetus clear motive lie {'neg': 0.48, 'neu': 0.379, 'pos': 0.141, 'compound': -0.7403}
right reversal pill result retarded baby want deal retarded burden mean save people head injury brain damage {'neg': 0.529, 'neu': 0.325, 'pos': 0.146, 'compound': -0.9153}
baby vote s need coddle make excuse----- {'neg': 0.0, 'neu': 0.794, 'pos': 0.206, 'compound': 0.0772}
kind funny conservative generally poor live area terrible {'neg':

[None, None, None, None, None, None, None, None, None, None]

In [ ]:
# sentiment score for each of my documents
# for each of my documents I have a certain set of topics
# will have a value for each document in terms of how much of topic 1 it is vs topic 2 for example
# then put into dataframe:
    # column with value for each topic (what percentage of each topic is the document) - so each topic has its own column
    # sentiment
# feed all of that into a classifier to make predictive model